In [ ]:
import sys
sys.path.append('..')
from tool import *

In [1]:
WB_pd=pd.read_csv('../data/desert_calibration.csv')
WB_sky_fraction=torch.load("/data/hk/albedo/white_sky_fraction/white_sky_fraction2.pth")
desert_coords=[[13.35,24.42],
               [23.39,28.55],
               [7.66,30.32],
               [2.23,31.02],
               [-9.3,19.4],
               [-8.78,20.85],
               [20.48,25.05],
               [26.10,27.12]]
WB_sky_fraction_desert=[]
for i in range(8):
    WB_sky_fraction_desert.append(WB_sky_fraction[:,90-int(desert_coords[i][1]),180+int(desert_coords[i][0])])
B_sky=[]
for i in range(8):
    B_sky.append(np.array(WB_pd[f'W{i+1}'])*WB_sky_fraction_desert[i]+np.array(WB_pd[f'B{i+1}'])*(1-WB_sky_fraction_desert[i]))

In [12]:
k=[]
for i in range(6):
    y=B_sky[i]
    slope, intercept, r_value, p_value, std_err = stats.linregress(list(range(240)), y)
    print(slope*12000/(y.mean()))
    k.append(slope*12000/(y.mean()))
print('mean:',np.array(k).mean())

-0.26028128869141764
-0.027183411041754677
0.2595175941514601
0.25202748602344455
-0.34061371681911595
0.6555468845451384
mean: 0.08983559136129245


In [14]:
desert_name=['Libya 1','Libya 2','Algeria 3','Algeria 5','Mauritannia 1','Mauritannia 2']
fig, axes = plt.subplots(3, 2, figsize=(16, 10),dpi=600)  # 3行2列布局，大小适当增加
for i, ax in enumerate(axes.flatten()):
    y=B_sky[i]
    slope, intercept, r_value, p_value, std_err = stats.linregress(list(range(240)), y/y.mean())
    print(slope*12000)
    date_range = pd.date_range(start='2001-01-01', end='2020-12-31', freq='M')
    df = pd.DataFrame({'Date': date_range, 'Value': y/y.mean()})
    slope*=12000
    sns.regplot(x=df.index, y='Value', data=df, scatter_kws={'s': 10}, line_kws={'color': 'red'},ax=ax)
    xtick_locs = np.array([  0,  24,  48,  72,  96, 120, 144, 168, 192, 216])  # 选择10个均匀分布的刻度
    xtick_labels = df['Date'].dt.strftime('%Y-%m').iloc[xtick_locs]  # 对应的日期标签
    ax.text(0.05, 0.95, f'Slope: {slope:.2f}% per decade', transform=ax.transAxes,
        fontsize=12, verticalalignment='top', bbox=dict(boxstyle='round,pad=0.3', facecolor='white', alpha=0.5))
    ax.set_xticks(ticks=xtick_locs, labels=xtick_labels, rotation=45)
    ax.set_ylim(0.9, 1.1)
    ax.set_title(f'Calibration error ({desert_name[i]})')
    ax.set_ylabel('Blue-sky albedo')
    ax.grid(True)
plt.tight_layout()
plt.savefig('../figure/calibration.pdf')
plt.show()

-0.26028128869141737
-0.027183411041753675
0.2595175941514607
0.2520274860234445
-0.34061371681911573
0.6555468845451391


In [15]:
k=[]
for i in [0,1,6,2,3,4,5,7]:
    y=B_sky[i]
    slope, intercept, r_value, p_value, std_err = stats.linregress(list(range(240)), y)
    print(slope*12000/(y.mean()))
    k.append(slope*12000/(y.mean()))
print('mean:',np.array(k).mean())

-0.26028128869141764
-0.027183411041754677
-0.011037743811799249
0.2595175941514601
0.25202748602344455
-0.34061371681911595
0.6555468845451384
-0.004604655478025556
mean: 0.06542139360974124


In [16]:
desert_name=['Libya 1','Libya 2','Libya 4','Algeria 3','Algeria 5','Mauritannia 1','Mauritannia 2','Egypt 1']
fig, axes = plt.subplots(4, 2, figsize=(16, 16),dpi=600)
for i, ax in enumerate(axes.flatten()):
    y=B_sky[i]
    slope, intercept, r_value, p_value, std_err = stats.linregress(list(range(240)), y/y.mean())
    print(slope*12000)
    date_range = pd.date_range(start='2001-01-01', end='2020-12-31', freq='M')
    df = pd.DataFrame({'Date': date_range, 'Value': y/y.mean()})
    slope*=12000
    sns.regplot(x=df.index, y='Value', data=df, scatter_kws={'s': 10}, line_kws={'color': 'red'},ax=ax)
    xtick_locs = np.array([  0,  24,  48,  72,  96, 120, 144, 168, 192, 216])  # 选择10个均匀分布的刻度
    xtick_labels = df['Date'].dt.strftime('%Y-%m').iloc[xtick_locs]  # 对应的日期标签
    ax.text(0.05, 0.95, f'Slope: {slope:.2f}% per decade', transform=ax.transAxes,
        fontsize=12, verticalalignment='top', bbox=dict(boxstyle='round,pad=0.3', facecolor='white', alpha=0.5))
    ax.set_xticks(ticks=xtick_locs, labels=xtick_labels, rotation=45)
    ax.set_ylim(0.9, 1.1)
    ax.set_title(f'Calibration error ({desert_name[i]})')
    ax.set_ylabel('Blue-sky albedo')
    ax.grid(True)
plt.tight_layout()
plt.savefig('../figure/calibration_8.pdf')
plt.show()

-0.26028128869141737
-0.027183411041753675
0.2595175941514607
0.2520274860234445
-0.34061371681911573
0.6555468845451391
-0.011037743811798591
-0.004604655478024259


In [17]:
result=torch.load('../data/albedo_change.pth')
calibration={}
for landcover_type in ['LCCS1','LCCS2','LCCS3','IGBP']:
    calibration[f'{landcover_type}_c_snow']=result[f'{landcover_type}_all_c'][0]
    calibration[f'{landcover_type}_s_snow']=result[f'{landcover_type}_all_s'][0]
    calibration[f'{landcover_type}_c_snowfree']=result[f'{landcover_type}_snowfree-change_c'][0]
    calibration[f'{landcover_type}_s_snowfree']=result[f'{landcover_type}_snowfree-change_s'][0]

In [18]:
desert_name=['LCCS1','LCCS2','LCCS3','IGBP']
fig, axes = plt.subplots(3, 2, figsize=(20, 14),dpi=600)
x=list(range(2001,2021))
for i, ax in enumerate(axes.flatten()):
    if i==4:
        break
    landcover_type=desert_name[i]
    kk=calibration[f'{landcover_type}_s_snowfree']
    ax.plot([0]+[kk[i]-kk[0] for i in range(1,20)],color='gray',label='Global albedo (no snow)')
    kk=calibration[f'{landcover_type}_c_snowfree']
    ax.plot([0]+[kk[i]-kk[0] for i in range(1,20)],color='gray',linestyle='--',label='Masked global albedo (no snow)')
    kk=calibration[f'{landcover_type}_s_snow']
    ax.plot([0]+[kk[i]-kk[0] for i in range(1,20)],color='plum',label='Global albedo')
    kk=calibration[f'{landcover_type}_c_snow']
    ax.plot([0]+[kk[i]-kk[0] for i in range(1,20)],color='plum',linestyle='--',label='Masked global albedo')
    ax.legend()
    ax.set_ylabel(f'ALLUM-{landcover_type}   '+r'short wave $\Delta \alpha$ ')
    ax.grid('-')
    ax.set_xticks(ticks=list(range(20)), labels=x, rotation=45)
axes = plt.subplot(313)
diff=[]
for i in range(4):
    kk=calibration[f'{landcover_type}_c_snowfree']
    kk2=calibration[f'{landcover_type}_s_snowfree']
    dif=np.array(kk2)-np.array(kk)
    diff.append(dif)
diff1=np.max(np.stack(diff),axis=0)
diff=[]
for i in range(4):
    kk=calibration[f'{landcover_type}_c_snow']
    kk2=calibration[f'{landcover_type}_s_snow']
    dif=np.array(kk2)-np.array(kk)
    diff.append(dif)
diff2=np.max(np.stack(diff),axis=0)
width = 0.25
x=np.array(list(range(2001,2021)))
axes.bar(x - width/2, diff1, width, label='Global albedo (no snow)',color='gray')
axes.bar(x + width/2, diff2, width, label='Global albedo',color='plum')
axes.legend()
axes.set_xticks(ticks=x, labels=list(range(2001,2021)), rotation=45)
axes.set_ylabel(r'calibation bias of global mean albedo')
axes.grid('-')
plt.savefig('../figure/robustness_calibration.pdf',dpi=600)